# Disease Classifier
## Modeling - Step 5 of Data Science Method
### Caitlin Ruble
### Capstone Project
#### Springboard Data Science Career Track


In this notebook I'll endeavor to optimize and evaluate at least 5 different types of models to determine which is the best. I'll be trying out a basic decision tree, a random forest classifier, an AdaBoost classifier, a Gradient Boost Classifier, and a SVM classifier. 

In [1]:
#Load in basic packages
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np

#import model selection functions
from sklearn.model_selection import train_test_split, GridSearchCV, RandomizedSearchCV

#import Supervised learning classifiers
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier, GradientBoostingClassifier
from sklearn.svm import SVC, LinearSVC

#import metrics functions
from sklearn.metrics import multilabel_confusion_matrix
from sklearn.metrics import accuracy_score
from sklearn.metrics import balanced_accuracy_score
from sklearn.metrics import f1_score
from sklearn.metrics import recall_score
from sklearn.metrics import precision_score
from sklearn.metrics import make_scorer

import time
from datetime import datetime


In [2]:
#load data and split into training and testing sets
train_data = pd.read_csv('data.csv')
X = train_data.drop(columns='prognosis')
y = train_data['prognosis']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state=0)

#load kaggle comparison data and split into X, y
kaggle_test = pd.read_csv('Testing.csv')
X_kag = kaggle_test.drop(columns='prognosis')
y_kag = kaggle_test['prognosis']

In [3]:
#initialize a results DataFrame to hold measures for comparison between models
results = pd.DataFrame(columns=['Model','Accuracy','Balanced Accuracy','F1','Precision','Recall','Training Time (s)', 'Prediction Time (s)'])

## Decision Tree - Entropy
Testing entropy model of tree classifier


In [4]:
#instantiate a decision tree
ent_tree = DecisionTreeClassifier(criterion = 'entropy', random_state=42)

#create param grid over which to grid search
params = {
          'max_depth': range(10,41,2),
          'min_samples_split': range(2, 403, 20),
          'min_samples_leaf': range(1,403, 20),
          'max_features': ['auto', 'sqrt'],
         }

cv_ent_tree = RandomizedSearchCV(ent_tree, params, random_state=42, n_iter = 200, cv=5)

#time the search
start_time = datetime.now()
cv_ent_tree.fit(X_train,y_train)
search_time = datetime.now() - start_time

print('Search Duration: {}'.format(search_time))
print(cv_ent_tree.best_params_)

Search Duration: 0:00:26.043290
{'min_samples_split': 82, 'min_samples_leaf': 1, 'max_features': 'auto', 'max_depth': 34}


In [5]:
#display the decision tree classifer 
from sklearn import tree
from io import StringIO  
from IPython.display import Image  
import pydotplus
import graphviz

#graph_viz will not support the cv_tree object from above, so I'm instantiating a new instance of the DecisionTreeClassifier using the tuned parameters found by CV, above
cv_ent_tree_graph = cv_ent_tree.best_estimator_

#fit to training data
cv_ent_tree_graph.fit(X_train,y_train)

# Now we want to visualize the tree
dot_data = StringIO()

# We can do so with export_graphviz
tree.export_graphviz(cv_ent_tree_graph, out_file=dot_data,  
                filled=True, rounded=True,
                special_characters=True, feature_names=X_train.columns, class_names = cv_ent_tree.classes_)
graph = graphviz.Source(dot_data)
graph

# Alternatively for class_names use entr_model.classes_
graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  
Image(graph.create_png())

In [6]:
#update tree model to reflect the tuned hyperparameters and fit to training data
#time the duration of training the model
start_time = time.time()
ent_tree = cv_ent_tree.best_estimator_.fit(X_train,y_train)
train_time = time.time()-start_time

#Evaluate model performance on test data

# Call predict() on cv_tree with X_test passed to it, and assign the result to a variable y_pred 
#time the prediction
start_time = time.time()
y_pred = ent_tree.predict(X_test)
predict_time = time.time()-start_time

#print metrics for review
print("Decision Tree - Entropy model - test data statistics")
print("Accuracy:", accuracy_score(y_test,y_pred))
print("Balanced accuracy:", balanced_accuracy_score(y_test,y_pred))
print('F1 score', f1_score(y_test,y_pred, average='macro'))
print("Precision score:" , precision_score(y_test,y_pred, average='macro'))
print("Precision score by category:" , precision_score(y_test,y_pred, average=None))
print("Recall score:" , recall_score(y_test,y_pred, average='macro'))
print("Recall score by category:" , recall_score(y_test,y_pred, average=None))


#add metrics to the results df
results.loc[len(results.index)] = ['Entropy Tree',
                                   accuracy_score(y_test,y_pred),
                                   balanced_accuracy_score(y_test,y_pred),
                                   f1_score(y_test,y_pred, average='macro'),
                                   precision_score(y_test,y_pred, average='macro'),
                                   recall_score(y_test,y_pred, average='macro'),
                                  np.round(train_time,2), np.round(predict_time,2)] 



Decision Tree - Entropy model - test data statistics
Accuracy: 0.9420731707317073
Balanced accuracy: 0.9447337369506664
F1 score 0.9464455711741189
Precision score: 0.9570543907537853
Precision score by category: [1.         0.46808511 0.90909091 1.         1.         1.
 0.93333333 1.         0.91304348 0.95238095 0.94444444 0.94736842
 1.         1.         1.         0.88       1.         0.89285714
 0.88235294 0.9047619  0.73913043 1.         0.95238095 1.
 1.         1.         1.         1.         0.92       1.
 1.         1.         1.         1.         1.         1.
 1.         1.         1.         1.         1.        ]
Recall score: 0.9447337369506664
Recall score by category: [0.94444444 1.         0.96774194 0.875      1.         0.95652174
 1.         0.92592593 1.         0.95238095 1.         1.
 0.95454545 1.         0.88888889 0.91666667 0.85185185 0.96153846
 0.9375     1.         1.         0.89285714 0.90909091 1.
 0.95652174 1.         0.95652174 0.88       0.88

## Decision Tree - Gini impurity
Testing gini impurity model of tree classifier


In [7]:
#instantiate a decision tree
gini_tree = DecisionTreeClassifier(criterion = 'gini', random_state=42)

#create param grid over which to grid search
params = {
          'max_depth': range(10,41,2),
          'min_samples_split': range(2, 403, 20),
          'min_samples_leaf': range(1,403, 20),
          'max_features': ['auto', 'sqrt'],
         }

#set up search
cv_gini_tree = RandomizedSearchCV(gini_tree, params, random_state=42, n_iter = 200, cv=5)

#time the search
start_time=datetime.now()
cv_gini_tree.fit(X_train,y_train)
search_time = datetime.now() - start_time

print('Search Duration: {}'.format(search_time))
print(cv_gini_tree.best_params_)

Search Duration: 0:00:19.702003
{'min_samples_split': 82, 'min_samples_leaf': 1, 'max_features': 'auto', 'max_depth': 34}


In [8]:
#display the decision tree classifer 
from sklearn import tree
from io import StringIO  
from IPython.display import Image  
import pydotplus
import graphviz

#graph_viz will not support the cv_tree object from above, so I'm instantiating a new instance of the DecisionTreeClassifier using the tuned parameters found by CV, above
cv_gini_tree_graph = cv_gini_tree.best_estimator_

#fit to training data
cv_gini_tree_graph.fit(X_train,y_train)

# Now we want to visualize the tree
dot_data = StringIO()

# We can do so with export_graphviz
tree.export_graphviz(cv_gini_tree_graph, out_file=dot_data,  
                filled=True, rounded=True,
                special_characters=True, feature_names=X_train.columns, class_names = cv_gini_tree.classes_)
graph = graphviz.Source(dot_data)
graph
graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  
Image(graph.create_png())

In [9]:
#update tree model to reflect the tuned hyperparameters and fit to training data
#time the duration of training the model
start_time = time.time()
ent_tree = cv_gini_tree.best_estimator_.fit(X_train,y_train)
train_time = time.time()-start_time


#Evaluate model performance on test data

# Call predict() on cv_tree with X_test passed to it, and assign the result to a variable y_pred 
start_time = time.time()
y_pred = cv_gini_tree.predict(X_test)
predict_time = time.time()-start_time


#print metrics
print("Decision Tree - Gini Impurity model - test data statistics")
print("Accuracy:", accuracy_score(y_test,y_pred))
print("Balanced accuracy:", balanced_accuracy_score(y_test,y_pred))
print('F1 score', f1_score(y_test,y_pred, average='macro'))
print("Precision score:" , precision_score(y_test,y_pred, average='macro'))
print("Precision score by category:" , precision_score(y_test,y_pred, average=None))
print("Recall score:" , recall_score(y_test,y_pred, average='macro'))
print("Recall score by category:" , recall_score(y_test,y_pred, average=None))


#add metrics to the results df
results.loc[len(results.index)] = ['Gini Impurity Tree',
                                   accuracy_score(y_test,y_pred),
                                   balanced_accuracy_score(y_test,y_pred),
                                   f1_score(y_test,y_pred, average='macro'),
                                   precision_score(y_test,y_pred, average='macro'),
                                   recall_score(y_test,y_pred, average='macro'),
                                   np.round(train_time,2), np.round(predict_time,2)] 

Decision Tree - Gini Impurity model - test data statistics
Accuracy: 0.9420731707317073
Balanced accuracy: 0.9425957276655904
F1 score 0.9504686356086657
Precision score: 0.969617716719917
Precision score by category: [1.         1.         1.         1.         0.92       0.92
 1.         1.         1.         0.86363636 1.         1.
 1.         1.         1.         0.36923077 0.92857143 1.
 0.96774194 1.         1.         1.         1.         1.
 1.         1.         1.         1.         1.         0.86206897
 1.         1.         1.         1.         1.         1.
 0.92307692 1.         1.         1.         1.        ]
Recall score: 0.9425957276655904
Recall score by category: [1.         0.77272727 0.93548387 0.91666667 1.         1.
 0.92857143 0.92592593 0.80952381 0.9047619  1.         1.
 1.         0.96296296 0.88888889 1.         0.96296296 0.96153846
 0.9375     1.         0.88235294 0.85714286 1.         1.
 1.         1.         1.         0.96       0.96153846 1.

## Random Forest Classifier

In [10]:
#instantiate a RandomForestClassifier
rf = RandomForestClassifier(random_state=42)

#create param grid over which to grid search
params = {'n_estimators':range(50,201,50),
          'criterion':['gini','entropy'],
          'max_depth': range(20,51,5),
          'min_samples_split': range(2, 103, 20),
          'min_samples_leaf': range(2,103, 20),
          'max_features': ['log2', 'sqrt']
         }

#set up search
cv_rf = RandomizedSearchCV(rf, params, random_state=42, n_iter = 100, cv=5)

#time the search
start_time = datetime.now()
cv_rf.fit(X_train,y_train)
search_time = datetime.now() - start_time

print('Search Duration: {}'.format(search_time))
print(cv_rf.best_params_)

Search Duration: 0:07:42.672639
{'n_estimators': 150, 'min_samples_split': 2, 'min_samples_leaf': 22, 'max_features': 'log2', 'max_depth': 25, 'criterion': 'gini'}


In [11]:
#update random forest model to reflect the tuned hyperparameters and fit to training data
#time the duration of training the model
start_time = time.time()
rf = cv_rf.best_estimator_.fit(X_train,y_train)
train_time = time.time()-start_time


#Evaluate model performance on test data

# Call predict() on cv_rf with X_test passed to it, and assign the result to a variable y_pred 
#time the prediction
start_time=time.time()
y_pred = rf.predict(X_test)
predict_time = time.time()-start_time

#print metrics
print("Random Forest model - test data statistics")
print("Accuracy:", accuracy_score(y_test,y_pred))
print("Balanced accuracy:", balanced_accuracy_score(y_test,y_pred))
print('F1 score', f1_score(y_test,y_pred, average='macro'))
print("Precision score:" , precision_score(y_test,y_pred, average='macro'))
print("Precision score by category:" , precision_score(y_test,y_pred, average=None))
print("Recall score:" , recall_score(y_test,y_pred, average='macro'))
print("Recall score by category:" , recall_score(y_test,y_pred, average=None))

#add metrics to the results df
results.loc[len(results.index)] = ['Random Forest',
                                   accuracy_score(y_test,y_pred),
                                   balanced_accuracy_score(y_test,y_pred),
                                   f1_score(y_test,y_pred, average='macro'),
                                   precision_score(y_test,y_pred, average='macro'),
                                   recall_score(y_test,y_pred, average='macro'),
                                  np.round(train_time,2), np.round(predict_time,2)] 



Random Forest model - test data statistics
Accuracy: 1.0
Balanced accuracy: 1.0
F1 score 1.0
Precision score: 1.0
Precision score by category: [1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.]
Recall score: 1.0
Recall score by category: [1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.]


Wow! The Random Forest Model gives 100% accuracy!

## Ada Boost Classifier

In [12]:
#instantiate an AdaBoostClassifier
ada = AdaBoostClassifier(random_state=42)



#create param grid over which to grid search
params = {'n_estimators':range(10,151,10),
          'learning_rate': np.arange(0.1,2.1,0.5)
         }

cv_ada = GridSearchCV(ada, params, cv=5)

#time the search
start_time=datetime.now()
cv_ada.fit(X_train,y_train)
search_time = datetime.now() - start_time


print('Search Duration: {}'.format(search_time))

print(cv_ada.best_params_)

Search Duration: 0:11:58.222692
{'learning_rate': 0.1, 'n_estimators': 140}


In [13]:
#because the learning rate is on the cusp of the parameter space, I'm going to do another search centered around that
#instantiate an AdaBoostClassifier
ada = AdaBoostClassifier(n_estimators=140, random_state=42)

#create param grid over which to grid search
params = {'learning_rate': np.arange(0.01,0.3,0.05)
         }

cv_ada = GridSearchCV(ada, params, cv=5)

#time the search
start_time=datetime.now()
cv_ada.fit(X_train,y_train)
search_time = datetime.now() - start_time


print('Search Duration: {}'.format(search_time))

print(cv_ada.best_params_)


Search Duration: 0:02:01.419277
{'learning_rate': 0.11}


In [14]:
#update AdaBoost model to reflect the tuned hyperparameters and fit to training data
#time the duration of training the model
start_time = time.time()
ada = cv_ada.best_estimator_.fit(X_train,y_train)
train_time = time.time()-start_time


#Evaluate model performance on test data

# Call predict() on ada with X_test passed to it, and assign the result to a variable y_pred 
#time the prediction
start_time = time.time()
y_pred = ada.predict(X_test)
predict_time = time.time() - start_time

print("AdaBoosted Decision Tree - test data statistics")
print("Accuracy:", accuracy_score(y_test,y_pred))
print("Balanced accuracy:", balanced_accuracy_score(y_test,y_pred))
print('F1 score', f1_score(y_test,y_pred, average='macro'))
print("Precision score:" , precision_score(y_test,y_pred, average='macro'))
print("Precision score by category:" , precision_score(y_test,y_pred, average=None))
print("Recall score:" , recall_score(y_test,y_pred, average='macro'))
print("Recall score by category:" , recall_score(y_test,y_pred, average=None))

results.loc[len(results.index)] = ['AdaBoosted Decision Tree',
                                   accuracy_score(y_test,y_pred),
                                   balanced_accuracy_score(y_test,y_pred),
                                   f1_score(y_test,y_pred, average='macro'),
                                   precision_score(y_test,y_pred, average='macro'),
                                   recall_score(y_test,y_pred, average='macro'),
                                  np.round(train_time,2), np.round(predict_time,2)] 

AdaBoosted Decision Tree - test data statistics
Accuracy: 0.9898373983739838
Balanced accuracy: 0.9891812388463613
F1 score 0.9902458990655042
Precision score: 0.9924858339492487
Precision score by category: [1.         1.         1.         1.         1.         1.
 1.         1.         1.         0.95454545 1.         1.
 1.         1.         1.         1.         1.         1.
 0.88888889 1.         1.         0.84848485 1.         1.
 1.         1.         1.         1.         1.         1.
 1.         1.         1.         1.         1.         1.
 1.         1.         1.         1.         1.        ]
Recall score: 0.9891812388463613
Recall score by category: [1.         1.         1.         1.         1.         1.
 1.         1.         1.         1.         1.         1.
 1.         1.         1.         1.         1.         1.
 1.         0.84210526 1.         1.         1.         1.
 1.         1.         1.         1.         0.88461538 1.
 1.         1.         1.  

## Gradient Boosting Classifier
"builds an additive model in a forward stage-wise fashion; it allows for the optimization of arbitrary differentiable loss functions. In each stage n_classes_ regression trees are fit on the negative gradient of the loss function, e.g. binary or multiclass log loss." - From [sklearn documentation](https://scikit-learn.org/stable/modules/generated/sklearn.ensemble.GradientBoostingClassifier.html?highlight=gradient%20boosting#sklearn.ensemble.GradientBoostingClassifier)

In [15]:
#instantiate a GradientBoostingClassifier
gb = GradientBoostingClassifier(random_state=42)

#create param grid over which to grid search
params = {
        'n_estimators': range(50,151,25),
        'learning_rate': np.arange(0.01,1.51,0.5),
        'max_depth': range(10,51,5),
        'min_samples_split': range(2, 103, 20),
        'min_samples_leaf': range(1,102, 20),
        'max_features': ['log2', 'sqrt',None]
         }

cv_gb = RandomizedSearchCV(gb, params, random_state=42, n_iter=60, cv=5)

#time the search
start_time = datetime.now()
cv_gb.fit(X_train,y_train)
search_time = datetime.now() - start_time


print('Search Duration: {}'.format(search_time))
print(cv_gb.best_params_)

Search Duration: 9:14:51.842978
{'n_estimators': 75, 'min_samples_split': 62, 'min_samples_leaf': 61, 'max_features': 'log2', 'max_depth': 50, 'learning_rate': 0.01}


In [16]:
#because some parameters were on the edge of the parameter space, 
#running another search to optimize those

gb = cv_gb.best_estimator_

params = {
        'learning_rate': np.arange(0.001,.011,0.002),
        'max_depth': range(50,76,5)
         }

cv_gb = GridSearchCV(gb, params, cv=5)

#time the search
start_time= datetime.now()
cv_gb.fit(X_train,y_train)
search_time = datetime.now() - start_time


print('Search Duration: {}'.format(search_time))

print(cv_gb.best_params_)

Search Duration: 1:21:15.135355
{'learning_rate': 0.001, 'max_depth': 50}


In [17]:
#update gb model to reflect the tuned hyperparameters and fit to training data
#time the duration of training the model
start_time = time.time()
gb = cv_gb.best_estimator_.fit(X_train,y_train)
train_time = time.time()-start_time


#Evaluate model performance on test data

# Call predict() on cv_rf with X_test passed to it, and assign the result to a variable y_pred 
#time it
start_time=time.time()
y_pred = gb.predict(X_test)
predict_time = time.time() - start_time


print("Gradient Boosted Decision Tree - test data statistics")
print("Accuracy:", accuracy_score(y_test,y_pred))
print("Balanced accuracy:", balanced_accuracy_score(y_test,y_pred))
print('F1 score', f1_score(y_test,y_pred, average='macro'))
print("Precision score:" , precision_score(y_test,y_pred, average='macro'))
print("Precision score by category:" , precision_score(y_test,y_pred, average=None))
print("Recall score:" , recall_score(y_test,y_pred, average='macro'))
print("Recall score by category:" , recall_score(y_test,y_pred, average=None))

results.loc[len(results.index)] = ['Gradient Boosted Decision Tree',
                                   accuracy_score(y_test,y_pred),
                                   balanced_accuracy_score(y_test,y_pred),
                                   f1_score(y_test,y_pred, average='macro'),
                                   precision_score(y_test,y_pred, average='macro'),
                                   recall_score(y_test,y_pred, average='macro'),
                                  np.round(train_time,2), np.round(predict_time,2)] 

Gradient Boosted Decision Tree - test data statistics
Accuracy: 1.0
Balanced accuracy: 1.0
F1 score 1.0
Precision score: 1.0
Precision score by category: [1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.]
Recall score: 1.0
Recall score by category: [1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.]


#### Summary: Gradient Boosting also yields perfect classification scores on the test data.

## RBF kernel SVM
C-Support Vector Classification.

The implementation is based on libsvm. The fit time scales at least quadratically with the number of samples and may be impractical beyond tens of thousands of samples. For large datasets consider using LinearSVC or SGDClassifier instead, possibly after a Nystroem transformer.

The multiclass support is handled according to a one-vs-one scheme.

Source: [sklearn documentation](https://scikit-learn.org/stable/modules/generated/sklearn.svm.SVC.html?highlight=svc#sklearn.svm.SVC)

In [18]:
#instantiate the SVC
svm = SVC(random_state=42)


#create param grid over which to grid search
params = {"C": [0.001, 0.01, 0.1, 1, 10],
          "degree": range(3,6),
          "gamma": ['scale','auto']
         }

cv_svm = GridSearchCV(svm, params, cv=5)

#time the search
start_time = datetime.now()
cv_svm.fit(X_train,y_train)
search_time = datetime.now() - start_time


print('Search Duration: {}'.format(search_time))
print(cv_svm.best_params_)


Search Duration: 0:36:06.790258
{'C': 0.1, 'degree': 3, 'gamma': 'scale'}


In [19]:
#update svm model to reflect the tuned hyperparameters and fit to training data
#time the duration of training the model
start_time = time.time()
svm = cv_svm.best_estimator_.fit(X_train,y_train)
train_time = time.time()-start_time

#Evaluate model performance on test data

# Call predict() on cv_rf with X_test passed to it, and assign the result to a variable y_pred 
#time the prediction
start_time = time.time()
y_pred = svm.predict(X_test)
predict_time = time.time()-start_time

print("SVM with RBF kernel - test data statistics")
print("Accuracy:", accuracy_score(y_test,y_pred))
print("Balanced accuracy:", balanced_accuracy_score(y_test,y_pred))
print('F1 score', f1_score(y_test,y_pred, average='macro'))
print("Precision score:" , precision_score(y_test,y_pred, average='macro'))
print("Precision score by category:" , precision_score(y_test,y_pred, average=None))
print("Recall score:" , recall_score(y_test,y_pred, average='macro'))
print("Recall score by category:" , recall_score(y_test,y_pred, average=None))

results.loc[len(results.index)] = ['SVM with RBF kernel',
                                   accuracy_score(y_test,y_pred),
                                   balanced_accuracy_score(y_test,y_pred),
                                   f1_score(y_test,y_pred, average='macro'),
                                   precision_score(y_test,y_pred, average='macro'),
                                   recall_score(y_test,y_pred, average='macro'),
                                  np.round(train_time,2), np.round(predict_time,2)] 

SVM with RBF kernel - test data statistics
Accuracy: 1.0
Balanced accuracy: 1.0
F1 score 1.0
Precision score: 1.0
Precision score by category: [1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.]
Recall score: 1.0
Recall score by category: [1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.]


#### Summary: SVM with an RBF kernel also yields perfect classification scores on the test data.

# Conclusions and Model Selection

Overall, there were 3 models that gave 100% accuracy on the test data: the Random Forest, the Gradient Boosted Decision Tree, and the SVM. This is great!

In order to make a conclusion about which model is "the best," we need to compare a different metric: the time to train and predict on samples. These measures would come into play in a production setting.

If we deploy a model that continuously retrains every time new data comes in, then we'd really value having a low training time. Because this is a medical diagnostic tool, we would probably retrain in careful batches to maintain control over the model, so training time is less important. **Amongst the top performing models, the Random Forest Model has the shortest training time and therefore wins by this measure.

What we're most interested in is the prediction time--which model can take new data and predict a class label the quickest. We measured the prediction time for the whole test set (984 samples), so we can think of the prediction time for a single prediction being the reported prediction time divided by 984. **Here, the Gradient Boosted Decision Tree wins, having the quickest run time for predicting a single occurence at 0.2 ms.

Overall, we have three great choices that produce 100% accuracy on the held-out testing set. The model chosen would depend on how the model is deployed: the GB tree has the quickest prediction time, but 25x the training time compared to the Random Forest and SVM. The training time might be prohibitively slow for retraining the model as the quantity of data increases. **Random Forest blends great prediction time (0.34 ms per patient) with a much lower training time (0.99s). By this logic, I deem it "the best" model and my recommended choice moving forward.


In [23]:
results['Prediction Time per Patient (ms)'] = results['Prediction Time (s)']/984*1000

In [25]:
results.sort_values(by='Accuracy', ascending=False)

Model  Accuracy  Balanced Accuracy        F1  \
2                   Random Forest  1.000000           1.000000  1.000000   
4  Gradient Boosted Decision Tree  1.000000           1.000000  1.000000   
5             SVM with RBF kernel  1.000000           1.000000  1.000000   
3        AdaBoosted Decision Tree  0.989837           0.989181  0.990246   
0                    Entropy Tree  0.942073           0.944734  0.946446   
1              Gini Impurity Tree  0.942073           0.942596  0.950469   

   Precision    Recall  Training Time (s)  Prediction Time (s)  \
2   1.000000  1.000000               0.99                 0.33   
4   1.000000  1.000000              24.38                 0.20   
5   1.000000  1.000000               1.09                 0.51   
3   0.992486  0.989181               8.18                 0.84   
0   0.957054  0.944734               0.02                 0.01   
1   0.969618  0.942596               0.02                 0.01   

   Prediction Time per Patient (ms)  
2                          0.335366  
4                          0.203252  
5                          0.518293  
3                          0.853659  
0                          0.010163  
1                          0.010163

## Test Kaggle hold-out data using the selected Model:

This part is mostly out of curiousity and so that I can upload this notebook back to the Kaggle dataset.

In [26]:
#import hold-out data
kaggle_test_data = pd.read_csv('testing.csv')

X_kag = kaggle_test_data.drop(columns='prognosis')
y_kag = kaggle_test_data['prognosis']

#make predictions using rf model
y_pred = rf.predict(X_kag)

print("Kaggle Hold-out Test Data with Random Forest model statistics")
print("Accuracy:", accuracy_score(y_kag,y_pred))
print("Balanced accuracy:", balanced_accuracy_score(y_kag,y_pred))
print('F1 score', f1_score(y_kag,y_pred, average='macro'))
print("Precision score:" , precision_score(y_kag,y_pred, average='macro'))
print("Precision score by category:" , precision_score(y_kag,y_pred, average=None))
print("Recall score:" , recall_score(y_kag,y_pred, average='macro'))
print("Recall score by category:" , recall_score(y_kag,y_pred, average=None))


Kaggle Hold-out Test Data with chosen model statistics
Accuracy: 0.9761904761904762
Balanced accuracy: 0.9878048780487805
F1 score 0.9837398373983739
Precision score: 0.9878048780487805
Precision score by category: [1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.
 1.  1.  1.  1.  1.  1.  1.  1.  1.  0.5 1.  1.  1.  1.  1.  1.  1.  1.
 1.  1.  1.  1.  1. ]
Recall score: 0.9878048780487805
Recall score by category: [1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  0.5 1.  1.
 1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.  1.
 1.  1.  1.  1.  1. ]


In [27]:
#with gb
y_pred = gb.predict(X_kag)

print("Kaggle Hold-out Test Data with GradientBoost model statistics")
print("Accuracy:", accuracy_score(y_kag,y_pred))
print("Balanced accuracy:", balanced_accuracy_score(y_kag,y_pred))
print('F1 score', f1_score(y_kag,y_pred, average='macro'))
print("Precision score:" , precision_score(y_kag,y_pred, average='macro'))
print("Precision score by category:" , precision_score(y_kag,y_pred, average=None))
print("Recall score:" , recall_score(y_kag,y_pred, average='macro'))
print("Recall score by category:" , recall_score(y_kag,y_pred, average=None))


Kaggle Hold-out Test Data with chosen model statistics
Accuracy: 1.0
Balanced accuracy: 1.0
F1 score 1.0
Precision score: 1.0
Precision score by category: [1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.]
Recall score: 1.0
Recall score by category: [1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.]


In [28]:
#with svm
y_pred = gb.predict(X_kag)

print("Kaggle Hold-out Test Data with SVM model statistics")
print("Accuracy:", accuracy_score(y_kag,y_pred))
print("Balanced accuracy:", balanced_accuracy_score(y_kag,y_pred))
print('F1 score', f1_score(y_kag,y_pred, average='macro'))
print("Precision score:" , precision_score(y_kag,y_pred, average='macro'))
print("Precision score by category:" , precision_score(y_kag,y_pred, average=None))
print("Recall score:" , recall_score(y_kag,y_pred, average='macro'))
print("Recall score by category:" , recall_score(y_kag,y_pred, average=None))


Kaggle Hold-out Test Data with SVM model statistics
Accuracy: 1.0
Balanced accuracy: 1.0
F1 score 1.0
Precision score: 1.0
Precision score by category: [1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.]
Recall score: 1.0
Recall score by category: [1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.]
